In [79]:
from pynq import Overlay
ol= Overlay('/home/xilinx/pynq/overlays/rrms/rrms.bit')

In [80]:
import pynq.lib.dma
dma=ol.axi_dma_sm
rr=ol.rrms_sm

In [81]:
from pynq import Xlnk
import numpy as np
xlnk = Xlnk()
xlnk?

In [82]:
a = xlnk.cma_array(shape=(5,), dtype=np.uint32)
b = xlnk.cma_array(shape=(5,), dtype=np.uint32)

In [83]:
for i in range(5):
  a[i]=i+2
    
a    

ContiguousArray([2, 3, 4, 5, 6], dtype=uint32)

In [84]:
rr.read(0x10)

0

In [85]:
dma.sendchannel.transfer(a)
dma.recvchannel.transfer(b)
dma.sendchannel.wait()
dma.recvchannel.wait()
b

ContiguousArray([2, 3, 4, 5, 6], dtype=uint32)

In [86]:
rr.read(0x10)

1

In [87]:
dma.sendchannel.transfer(a)
dma.recvchannel.transfer(b)
dma.sendchannel.wait()
dma.recvchannel.wait()
b
rr.read(0x10)

2

In [12]:
dma.sendchannel.transfer(a)
dma.recvchannel.transfer(b)
dma.sendchannel.wait()
dma.recvchannel.wait()
b
rr.read(0x10)

3

In [89]:
dma.sendchannel.transfer(a)
dma.recvchannel.transfer(b)
dma.sendchannel.wait()
dma.recvchannel.wait()
b
rr.read(0x10)

4

In [90]:
dma.sendchannel.transfer(a)
dma.recvchannel.transfer(b)
dma.sendchannel.wait()
dma.recvchannel.wait()
b
rr.read(0x10)

0

In [91]:
dma.sendchannel.transfer(a)
dma.recvchannel.transfer(b)
dma.sendchannel.wait()
dma.recvchannel.wait()
b
rr.read(0x10)

1

In [92]:
from pynq import DefaultIP
class RRDriver(DefaultIP):
    
    def __init__(self, description):
        super().__init__(description=description)
        
    bindto = ['xilinx.com:hls:rrms:1.0']

    @property
    def index(self):
        return self.read(0x10)
    

In [93]:
ol= Overlay('/home/xilinx/pynq/overlays/rrms/rrms.bit')
ol.ip_dict

{'axi_dma_sm': {'addr_range': 65536,
  'driver': pynq.lib.dma.DMA,
  'fullpath': 'axi_dma_sm',
  'gpio': {},
  'interrupts': {},
  'phys_addr': 1077936128,
  'state': None,
  'type': 'xilinx.com:ip:axi_dma:7.1'},
 'rrms_sm': {'addr_range': 65536,
  'driver': __main__.RRDriver,
  'fullpath': 'rrms_sm',
  'gpio': {},
  'interrupts': {},
  'phys_addr': 1136656384,
  'state': None,
  'type': 'xilinx.com:hls:rrms:1.0'}}

In [94]:
help(ol)


Help on Overlay in module pynq.overlay object:

class Overlay(pynq.pl.Bitstream)
 |  Default documentation for overlay /home/xilinx/pynq/overlays/rrms/rrms.bit. The following
 |  attributes are available on this overlay:
 |  
 |  IP Blocks
 |  ----------
 |  axi_dma_sm           : pynq.lib.dma.DMA
 |  rrms_sm              : __main__.RRDriver
 |  
 |  Hierarchies
 |  -----------
 |  None
 |  
 |  Interrupts
 |  ----------
 |  None
 |  
 |  GPIO Outputs
 |  ------------
 |  None
 |  
 |  Method resolution order:
 |      Overlay
 |      pynq.pl.Bitstream
 |      builtins.object
 |  
 |  Methods defined here:
 |  
 |  __dir__(self)
 |      __dir__() -> list
 |      default dir() implementation
 |  
 |  __getattr__(self, key)
 |      Overload of __getattr__ to return a driver for an IP or
 |      hierarchy. Throws an `RuntimeError` if the overlay is not loaded.
 |  
 |  __init__(self, bitfile_name, download=True, ignore_version=False)
 |      Return a new Overlay object.
 |      
 |      An

In [95]:
import pynq.lib.dma
dma1=ol.axi_dma_sm
rr1=ol.rrms_sm

In [96]:
from pynq import Xlnk
import numpy as np

xlnk = Xlnk()
in_buffer = xlnk.cma_array(shape=(5,), dtype=np.uint32)
out_buffer = xlnk.cma_array(shape=(5,), dtype=np.uint32)

for i in range(5):
    in_buffer[i] = i


dma1.sendchannel.transfer(in_buffer)
dma1.recvchannel.transfer(out_buffer)
dma1.sendchannel.wait()
dma1.recvchannel.wait()

out_buffer

ContiguousArray([0, 1, 2, 3, 4], dtype=uint32)

In [97]:
from pynq import DefaultHierarchy

class StreamRRDriver(DefaultHierarchy):
    def __init__(self, description):
        super().__init__(description)    
       
    def stream_rr(self, stream, index):
        index=self.rrms.index
        with xlnk.cma_array(shape=(len(stream),), dtype=np.uint32) as in_buffer,\
             xlnk.cma_array(shape=(len(stream),), dtype=np.uint32) as out_buffer:
            for i, v, in enumerate(stream):
                in_buffer[i] = v
            self.axi_dma_sm.sendchannel.transfer(in_buffer)
            self.axi_dma_sm.recvchannel.transfer(out_buffer)
            self.axi_dma_sm.sendchannel.wait()
            self.axi_dma_sm.recvchannel.wait()
            result = out_buffer.copy()
            
        return result, index

    @staticmethod
    def checkhierarchy(description):
        if 'axi_dma_sm' in description['ip'] and 'rrms_sm' in description['ip']:
            return True
        return False

In [99]:
ol= Overlay('/home/xilinx/pynq/overlays/rrms/rrms.bit')
help(ol)

Help on Overlay in module pynq.overlay object:

class Overlay(pynq.pl.Bitstream)
 |  Default documentation for overlay /home/xilinx/pynq/overlays/rrms/rrms.bit. The following
 |  attributes are available on this overlay:
 |  
 |  IP Blocks
 |  ----------
 |  axi_dma_sm           : pynq.lib.dma.DMA
 |  rrms_sm              : __main__.RRDriver
 |  
 |  Hierarchies
 |  -----------
 |  None
 |  
 |  Interrupts
 |  ----------
 |  None
 |  
 |  GPIO Outputs
 |  ------------
 |  None
 |  
 |  Method resolution order:
 |      Overlay
 |      pynq.pl.Bitstream
 |      builtins.object
 |  
 |  Methods defined here:
 |  
 |  __dir__(self)
 |      __dir__() -> list
 |      default dir() implementation
 |  
 |  __getattr__(self, key)
 |      Overload of __getattr__ to return a driver for an IP or
 |      hierarchy. Throws an `RuntimeError` if the overlay is not loaded.
 |  
 |  __init__(self, bitfile_name, download=True, ignore_version=False)
 |      Return a new Overlay object.
 |      
 |      An

In [100]:
ol.ip_dict

{'axi_dma_sm': {'addr_range': 65536,
  'driver': pynq.lib.dma.DMA,
  'fullpath': 'axi_dma_sm',
  'gpio': {},
  'interrupts': {},
  'phys_addr': 1077936128,
  'state': None,
  'type': 'xilinx.com:ip:axi_dma:7.1'},
 'rrms_sm': {'addr_range': 65536,
  'driver': __main__.RRDriver,
  'fullpath': 'rrms_sm',
  'gpio': {},
  'interrupts': {},
  'phys_addr': 1136656384,
  'state': None,
  'type': 'xilinx.com:hls:rrms:1.0'}}

In [101]:
index=1
ol.rrms_sm.stream_rr([1,2,3,4,5], index)

AttributeError: 'RRDriver' object has no attribute 'stream_rr'